In [1]:
  pip install backtesting

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 175.5/175.5 kB 2.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for backtesting: filename=Backtesting-0.3.3-py3-none-any.whl size=173916 sha256=3978f2ba4eb9eb581f884031feba2a81f36346bd49e17087c586b6c8b68f9f59
  Stored in directory: /root/.cache/pip/wheels/e2/30/7f/19cbe31987c6ebdb47f1f510343249066711609e3da2d57176
Successfully built backtesting


In [2]:
!pip install pandas_ta

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.1/115.1 kB 1.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pandas_ta: filename=pandas_ta-0.3.14b0-py3-none-any.whl size=218907 sha256=649a1ec1ca825377143aaf3d1966d32bc544dcaa05100c7b5a37e690a2fee2e0
  Stored in directory: /root/.cache/pip/wheels/69/00/ac/f7fa862c34b0e2ef320175100c233377b4c558944f12474cf0
Successfully built pandas_ta


In [3]:
from IPython.core.display import display, HTML
from backtesting import Backtest, Strategy
from backtesting.lib import crossover
import pandas as pd
import numpy as np
import plotly.express as px
import seaborn as sns
import matplotlib.pyplot as plt
import datetime as dt
#import talib
import pandas_ta as ta
from scipy import stats

/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:50: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


In [4]:
btc = pd.read_csv('cleaned-bitcoin-transfer-volume-from-miners-to-exchanges-usd-all-exchanges-1h-filtered-period.csv', index_col=0, parse_dates=True)

display(btc.info())
display(btc)

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 25337 entries, 2021-01-01 00:00:00+00:00 to 2023-11-22 16:00:00+00:00
Data columns (total 5 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   transfer  25337 non-null  float64
 1   Close     25337 non-null  float64
 2   High      25337 non-null  float64
 3   Low       25337 non-null  float64
 4   Open      25337 non-null  float64
dtypes: float64(5)
memory usage: 1.2 MB


None

transfer        Close         High  \
timestamp                                                           
2021-01-01 00:00:00+00:00  8.708823e+04  28996.63382  29016.64762   
2021-01-01 01:00:00+00:00  5.514015e+04  29398.95150  29424.86270   
2021-01-01 02:00:00+00:00  1.287187e+06  29314.39314  29422.38170   
2021-01-01 03:00:00+00:00  4.455728e+04  29290.97846  29335.01014   
2021-01-01 04:00:00+00:00  5.894313e+06  29248.35693  29391.26768   
...                                 ...          ...          ...   
2023-11-22 12:00:00+00:00  0.000000e+00  36581.02379  36581.02379   
2023-11-22 13:00:00+00:00  0.000000e+00  36630.52274  36630.52274   
2023-11-22 14:00:00+00:00  2.761576e+05  36347.39527  36619.09436   
2023-11-22 15:00:00+00:00  0.000000e+00  36466.92461  36598.77251   
2023-11-22 16:00:00+00:00  0.000000e+00  36553.72702  36554.54231   

                                   Low         Open  
timestamp                                            
2021-01-01 00:00:00+00:00  28822.72449  29001.71982  
2021-01-01 01:00:00+00:00  29032.31198  29032.31198  
2021-01-01 02:00:00+00:00  29252.18529  29411.56663  
2021-01-01 03:00:00+00:00  29228.78944  29228.78944  
2021-01-01 04:00:00+00:00  29178.97329  29330.33371  
...                                ...          ...  
2023-11-22 12:00:00+00:00  36469.51851  36469.51851  
2023-11-22 13:00:00+00:00  36478.26588  36570.01111  
2023-11-22 14:00:00+00:00  36347.39527  36619.09436  
2023-11-22 15:00:00+00:00  36255.28583  36399.72941  
2023-11-22 16:00:00+00:00  36490.57711  36490.57711  

[25337 rows x 5 columns]

In [5]:
btc["transfer"].mean()

260240.56917027742

In [6]:
btc['z_score'] = stats.zscore(btc['transfer'])

In [7]:
btc.head()

transfer        Close         High  \
timestamp                                                           
2021-01-01 00:00:00+00:00  8.708823e+04  28996.63382  29016.64762   
2021-01-01 01:00:00+00:00  5.514015e+04  29398.95150  29424.86270   
2021-01-01 02:00:00+00:00  1.287187e+06  29314.39314  29422.38170   
2021-01-01 03:00:00+00:00  4.455728e+04  29290.97846  29335.01014   
2021-01-01 04:00:00+00:00  5.894313e+06  29248.35693  29391.26768   

                                   Low         Open   z_score  
timestamp                                                      
2021-01-01 00:00:00+00:00  28822.72449  29001.71982 -0.137119  
2021-01-01 01:00:00+00:00  29032.31198  29032.31198 -0.162419  
2021-01-01 02:00:00+00:00  29252.18529  29411.56663  0.813238  
2021-01-01 03:00:00+00:00  29228.78944  29228.78944 -0.170799  
2021-01-01 04:00:00+00:00  29178.97329  29330.33371  4.461616

In [8]:
class TransferFromMiners(Strategy):
  zscore_param = 2
  upper_bound = 70
  lower_bound = 20
  rsi_window = 4

  def init(self):
    self.zscore = self.I(lambda df: df["z_score"], self.data.df)
    self.transfer = self.I(lambda df: df["transfer"], self.data.df)
    self.rsi = self.I(lambda df: df.ta.rsi(self.rsi_window), self.data.df)

#Strategy logic
  def next(self):
    zscore_now = self.zscore[-1]
    transfer_now = self.transfer[-1]
    price = self.data.Close[-1]
    if zscore_now > self.zscore_param:
      self.sell(size=1, tp= price * 0.5, sl= price * 1.02)
    elif crossover(self.lower_bound, self.rsi):
      self.position.close()

bt = Backtest(btc, TransferFromMiners, cash = 100000, commission=0.001)

#Optimizing the parameters, below is for demonstration purpose, you may use a much broader range initially.
btstats, btheatmap = bt.optimize(
    zscore_param = list(np.linspace(1.5, 3, num=10)),
    lower_bound = range(20,26,2),
    rsi_window = range(3,5,1),
    maximize = 'Sharpe Ratio',
    return_heatmap = True
)

print(btstats)

Backtest.optimize:   0%|          | 0/2 [00:00<?, ?it/s]

Start                     2021-01-01 00:00...
End                       2023-11-22 16:00...
Duration                   1055 days 16:00:00
Exposure Time [%]                   10.320875
Equity Final [$]                153326.315688
Equity Peak [$]                 155088.060869
Return [%]                          53.326316
Buy & Hold Return [%]               26.061967
Return (Ann.) [%]                    15.91971
Volatility (Ann.) [%]               11.192355
Sharpe Ratio                         1.422374
Sortino Ratio                        2.946076
Calmar Ratio                         2.299701
Max. Drawdown [%]                   -6.922512
Avg. Drawdown [%]                   -1.060647
Max. Drawdown Duration      583 days 07:00:00
Avg. Drawdown Duration       12 days 04:00:00
# Trades                                  314
Win Rate [%]                        60.828025
Best Trade [%]                       9.598493
Worst Trade [%]                     -3.833381
Avg. Trade [%]                    

In [9]:
btstats['_strategy']

<Strategy TransferFromMiners(zscore_param=2.1666666666666665,lower_bound=24,rsi_window=4)>

In [10]:
btstats["_trades"].sort_values(by="EntryTime")

Size  EntryBar  ExitBar    EntryPrice     ExitPrice          PnL  \
1      -1        56       65  34205.344925  32762.267550  1443.077375   
0      -1        57       65  34272.591452  32762.267550  1510.323902   
2      -1        82       86  30948.778632  31711.900939  -763.122308   
3      -1       140      141  35225.517781  36190.004226  -964.486445   
4      -1       146      147  36934.016572  37598.936846  -664.920273   
..    ...       ...      ...           ...           ...          ...   
312    -1     25272    25308  37314.555433  37179.243130   135.312303   
311    -1     25282    25308  37181.341270  37179.243130     2.098140   
310    -1     25296    25308  37431.690550  37179.243130   252.447420   
309    -1     25306    25308  37286.248418  37179.243130   107.005288   
313    -1     25330    25336  36661.098853  36490.577110   170.521743   

     ReturnPct                 EntryTime                  ExitTime  \
1     0.042189 2021-01-03 08:00:00+00:00 2021-01-03 17:00:00+00:00   
0     0.044068 2021-01-03 09:00:00+00:00 2021-01-03 17:00:00+00:00   
2    -0.024658 2021-01-04 10:00:00+00:00 2021-01-04 14:00:00+00:00   
3    -0.027380 2021-01-06 20:00:00+00:00 2021-01-06 21:00:00+00:00   
4    -0.018003 2021-01-07 02:00:00+00:00 2021-01-07 03:00:00+00:00   
..         ...                       ...                       ...   
312   0.003626 2023-11-20 00:00:00+00:00 2023-11-21 12:00:00+00:00   
311   0.000056 2023-11-20 10:00:00+00:00 2023-11-21 12:00:00+00:00   
310   0.006744 2023-11-21 00:00:00+00:00 2023-11-21 12:00:00+00:00   
309   0.002870 2023-11-21 10:00:00+00:00 2023-11-21 12:00:00+00:00   
313   0.004651 2023-11-22 10:00:00+00:00 2023-11-22 16:00:00+00:00   

           Duration  
1   0 days 09:00:00  
0   0 days 08:00:00  
2   0 days 04:00:00  
3   0 days 01:00:00  
4   0 days 01:00:00  
..              ...  
312 1 days 12:00:00  
311 1 days 02:00:00  
310 0 days 12:00:00  
309 0 days 02:00:00  
313 0 days 06:00:00  

[314 rows x 10 columns]

In [11]:
bt.plot(resample=False)

/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%d %b'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:250: UserWarning: DatetimeFormatter scales now only accept a single format. Using the first provided: '%m/%Y'
  formatter=DatetimeTickFormatter(days=['%d %b', '%a %d'],
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  fig = gridplot(
/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:659: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  fig = gridplot(


GridPlot(id='p1398', ...)